---

# S03E06 : Functions & Decorators - Advanced decorator

Cyril Desjouy

---

As you have seen previously, the use of a decorator is a simple and effective way to factor code and facilitate its reuse. In this notebook, we will continue the discovery of this type of functions through some recipes to create decorators:

* taking their own input arguments,
* keeping track of their status through function attributes,
* adding input arguments to the ***wrapper*** function.

As you will have understood, this list is not exhaustive, and the possibilities offered by decorators are endless!


## 1. Decorators with arguments

It often happens that it is necessary to pass one or more input arguments to a decorator in order to customize the way the decoration is done. In this case, the decorator and his ***wrapper*** are usually surrounded by an additional function whose objective is to manage the arguments. 

The following example will serve as a basis for understanding the mechanisms involved when creating a decorator with an input argument:

In [18]:
import functools

def fancy(char='*', n=80):
    def decorator(func):
        @functools.wraps(func)
        def wrapper(*args, **kwargs):
            print(n*char + f'\nExecuting {func.__name__}')
            value = func(*args, **kwargs)
            print(f'Output:{value}\n' + n*char)
            return value
        return wrapper
    return decorator

@fancy('*')
def multiply(x, y):
    return x*y

results = multiply(2, 3)

********************************************************************************
Executing multiply
Output:6
********************************************************************************


* The inner `wrapper` function is not very different from those we saw earlier. The variables `n` and `char` are found by the interpreter in a higher ***scope***, the one of `fancy` which is a ***enclosed scope***.
* The `decorator` function is exactly the same as the one seen above. It takes the function `func` as an input argument and returns a reference to the `wrapper`.
* The `fancy` function is only an additional layer to retrieve the input arguments that will be made available in the lower ***scopes***. This function returns a reference to the `decorator`.
* The use of the `@fancy` decorator is now done with `( )` (and possible input arguments). In the previous examples the decorators were used without brackets to refer to the decoration function. In this case, to refer to the decoration function, it is necessary to call the `fancy` function **with its input arguments**. 
* The variables `char` and `n` are passed to the lower ***scopes***. A ***closure*** is then created.

If the decorator is called without arguments, an exception is raised. As mentioned above, it is absolutely necessary that the `fancy` function be **called** to return the reference to `decorator`.

However, it is possible to create decorators that can be used with or without arguments.

<div class="alert alert-block alert-info">
Test the following example by modifying <code>@fancy</code>. 
</div>

In [15]:
import functools

def fancy(func=None, char='*', n=80):
    def decorator(func):
        @functools.wraps(func)
        def wrapper(*args, **kwargs):
            print(n*char + f'\nExecuting {func.__name__}')
            value = func(*args, **kwargs)
            print(f'Output:{value}\n' + n*char)
            return value
        return wrapper
    
    if func:
        return decorator(func)
    
    return decorator

@fancy
def multiply(x, y):
    return x*y

results = multiply(2, 3)



********************************************************************************
Executing multiply
Output:6
********************************************************************************


The `fancy` function then takes the function to be decorated as an optional input argument (`function`). 
If this argument is provided, `fancy` **calls** `decorator`. If it is not provided, it just returns a **reference** to `decorator`. It is thus possible to use `@fancy` with or without parenthesis!

Note that an excellent alternative writing using ***partial functions*** is offered in the *[Python cookbook](https://d.cxcore.net/Python/Python_Cookbook_3rd_Edition.pdf)* (Recipe 9.6):

In [56]:
def fancy(func=None, char='*', n=80):
    
    if func is None:
         return functools.partial(fancy, char=char, n=n)

    @functools.wraps(func)
    def wrapper(*args, **kwargs):
        print(n*char + f'\nExecuting {func.__name__}')
        value = func(*args, **kwargs)
        print(f'Output:{value}\n' + n*char)
        return value
    
    return wrapper

@fancy(char='-', n=20)
def multiply(x, y):
    return x*y

results = multiply(2, 3)

--------------------
Executing multiply
Output:6
--------------------


## 2. Decorator keeping track of his condition

Functions, like any object in Python, have attributes. It is possible to create a new function attribute as follows:
```python
def func():
    pass

func.attribute = 'attribute'
print(func.attribute)        # display 'attribute'
```

To go further, it is also possible to act on this attribute from the function:
```python
def counter():
    counter.count += 1
    print(counter.count)
    
counter.count = 0 
```

```python
>> counter()
1
>> counter()
2
>> counter()
3
...
```
Just keep in mind that these function attributes are initialized outside the function. They can then be modified in the function. This mechanism makes it easy to create decorators that keep track of a state. For example:

In [23]:
import functools

def count(func):
    @functools.wraps(func)
    def wrapper(*args, **kwargs):
        wrapper.calls += 1
        print(f"Call {wrapper.calls} of {func.__name__!r} function")
        return func(*args, **kwargs)
    wrapper.calls = 0
    return wrapper

@count
def hello():
    print("Hello world!")
    
for i in range(3):
    hello()

Call 1 of 'hello' function
Hello world!
Call 2 of 'hello' function
Hello world!
Call 3 of 'hello' function
Hello world!


## 3. Decorator adding arguments 

It is quite possible to create a decorator to add an optional argument to the function to be decorated. To do this, simply add this argument directly to `wrapper`:

In [36]:
import functools

def verbose(func):    
    @functools.wraps(func)
    def wrapper(*args, level=0, **kwargs):
        if level == 1:
            print(f'Calling {func.__name__}')
        if level == 2:
            print(f'Calling {func.__name__} with')
            print(f'\t* {str(args)} as positional arguments')
            print(f'\t* {str(kwargs)} as keyword arguments')
        return func(*args, **kwargs)
    return wrapper

@verbose
def stuff(task, like_a=''):
    print(f'Doing {task} like a {like_a}'.center(80))

print('Without argument level:')
stuff('Python', like_a='boss')

print('\nWith argument level:')
stuff('Python', like_a='boss', level=2)

Without argument level:
                            Doing Python like a boss                            

With argument level:
Calling stuff with
	* ('Python',) as positional arguments
	* {'like_a': 'boss'} as keyword arguments
                            Doing Python like a boss                            


## Application

<div class="alert alert-block alert-info">
Write a decorator to measure the time it takes for a function to execute. 
The decorator will keep a record of all measured times. The decorator will work as follows if used without an input argument:
</div>

```python
@timing
def mult(x, y):
    return x*y

>> m1 = mult(2, 4)
>> m2 = mult(2, 4)
>> print(mult.log)
{}
```
<div class="alert alert-block alert-info">
and as follows if used with the argument <code>log</code> being <code>True</code>
</div>


```python
@timing(log=True)
def mult(x, y):
    return x*y

>> m1 = mult(2, 4)
>> m2 = mult(2, 4)
>> print(mult.log)
{'mult1': 2.843968104571104e-06, 'mult2': 1.5129917301237583e-06}
```

## References

* [Python Cookbook - Recipe 9.6](https://d.cxcore.net/Python/Python_Cookbook_3rd_Edition.pdf)
* [Real Python - Primer on Python decorators](https://realpython.com/primer-on-python-decorators/)